# Lecture 19: Spark Structured Streaming

## Learning objectives

By the end of this lecture, students should be able to:
- Understand the key components of a Spark Streaming job
- Set up a sample word count streaming application
- Set up a sample device reading streaming application

## Learning resources

Please check out Spark documentation for a comprehensive explanation of Spark Streaming

https://spark.apache.org/docs/3.4.0/structured-streaming-programming-guide.html

## Environment set up 



### Install `ncat`

`Netcat` (commonly abbreviated as `nc`) is a versatile networking tool used for reading from and writing to network connections using TCP or UDP. 

In this worksheet, you can use `netcat` to simulate a text stream by sending data over a network socket. This is particularly useful when testing real-time streaming applications that require a continuous data flow, like Spark Streaming applications.

1. Install ncat by downloading it from https://nmap.org/download.html
2. Double check if ncat has been installed successfully by typing `ncat -v`. This should print out the ncat version 7.80 or higher

## Spark Streaming basics

Sensors, IoT devices, social networks, and online transactions all generate data that needs to be monitored constantly and acted upon quickly. As a result, the need for large-scale, real-time stream processing is more evident than ever before. 

At a high level, Spark Streaming receives live input data streams and divides the data into batches, which are then processed by the Spark engine to generate the final stream of results in batches.

![](https://spark.apache.org/docs/latest/img/streaming-flow.png)

The key idea in Structured Streaming is to treat a live data stream as a table that is being continuously appended. This leads to a new stream processing model that is very similar to a batch processing model. You will express your streaming computation as standard batch-like query as on a static table, and Spark runs it as an incremental query on the unbounded input table. Let’s understand this model in more detail.

![](https://spark.apache.org/docs/3.4.0/img/structured-streaming-stream-as-a-table.png)

A query on the input will generate the “Result Table”. Every trigger interval (say, every 1 second), new rows get appended to the Input Table, which eventually updates the Result Table. Whenever the result table gets updated, we would want to write the changed result rows to an external sink.

![](https://spark.apache.org/docs/3.4.0/img/structured-streaming-model.png)

The “Output” is defined as what gets written out to the external storage. The output can be defined in a different mode:

- **Complete Mode** - The entire updated Result Table will be written to the external storage. It is up to the storage connector to decide how to handle writing of the entire table.
- **Append Mode** - Only the new rows appended in the Result Table since the last trigger will be written to the external storage. This is applicable only on the queries where existing rows in the Result Table are not expected to change.
- **Update Mode** - Only the rows that were updated in the Result Table since the last trigger will be written to the external storage (available since Spark 2.1.1). Note that this is different from the Complete Mode in that this mode only outputs the rows that have changed since the last trigger. If the query doesn’t contain aggregations, it will be equivalent to Append mode.

![](https://spark.apache.org/docs/3.4.0/img/structured-streaming-example-model.png)

## Example 1: Real-time word count application

Let's initialize a SparkSession

In [39]:
from pyspark.sql import SparkSession

spark = SparkSession.builder \
    .appName("WordCountStreaming") \
    .getOrCreate()

# Set the number of shuffle partitions
spark.conf.set("spark.sql.shuffle.partitions", "4")

24/11/20 12:08:40 WARN SparkSession: Using an existing Spark session; only runtime SQL configurations will take effect.


> `spark.sql.shuffle.partitions`
> 
> This configuration property determines the number of partitions to use when shuffling data for joins or aggregations. By default, Spark sets this to 200, but it can be adjusted based on the size of the data and the cluster resources.

In [40]:
spark

Let's read in the sample text file in `data/input/sample.txt`

In [41]:
# read input data
# lines = spark.read.format("text").load("data/sample.txt")

# # Define the streaming source (ncat on port 9999)
lines = spark.readStream \
    .format("socket") \
    .option("host", "localhost") \
    .option("port", 9999) \
    .load()

24/11/20 12:08:43 WARN TextSocketSourceProvider: The socket source should not be used for production applications! It does not support recovery.


In [ ]:
# lines.show()

`.format("socket")`:

- Specifies the format of the streaming source.
- "socket" indicates that the source is a socket stream, which means data will be read from a TCP socket.

Other options for format include:
- **Socket**: Reads data from a TCP socket.
- **Kafka**: Reads data from a Kafka topic.
- **File Source**: Reads data from files (CSV, JSON, Parquet).
- **Rate Source**: Generates data at a fixed rate (useful for testing).
- **Delta Lake**: Reads data from Delta Lake tables.
- **Custom Source**: Allows for custom data source implementations.

`.option("host", "localhost")`:

- Sets the host option for the socket source.
- `"localhost"` specifies that the data will be read from a socket on the local machine.

`.option("port", "9999")`:

- Sets the port option for the socket source.
- `"9999"` specifies that the data will be read from port 9999 on the local machine.

In [ ]:
# lines.printSchema()

In [ ]:
# lines.show()

In [42]:
# split the line into words
from pyspark.sql.functions import split, explode, col

# Split the lines into words
words = lines.select(explode(split(col("value"), " ")).alias("word"))

# words.show()

In [43]:
# Count occurrences of each word
word_counts = words.groupBy("word").count()
# word_counts.show()

Before excecute the next cell, you will need to activate netcat by typing in the terminal `ncat -l 9999`.

The command `ncat -l 9999` is used to start a simple TCP server that listens for incoming connections on port 9999.

In [45]:
# Write the output to the console
query = word_counts.writeStream \
    .format("console") \
    .outputMode("complete") \
    .start()

query.awaitTermination()

24/11/20 12:09:10 WARN ResolveWriteToStream: Temporary checkpoint location created which is deleted normally when the query didn't fail: /private/var/folders/vs/gmr4pxqx5fjg8p7kzzwgwqbw0000gn/T/temporary-883f3863-e9db-43ca-9e27-54d26839c9db. If it's required to delete it under any circumstances, please set spark.sql.streaming.forceDeleteTempCheckpointLocation to true. Important to know deleting temp checkpoint folder is best effort.
24/11/20 12:09:10 WARN ResolveWriteToStream: spark.sql.adaptive.enabled is not supported in streaming DataFrames/Datasets and will be disabled.


-------------------------------------------
Batch: 0
-------------------------------------------
+----+-----+
|word|count|
+----+-----+
+----+-----+

-------------------------------------------
Batch: 1
-------------------------------------------
+----+-----+
|word|count|
+----+-----+
| cat|    1|
| dog|    1|
+----+-----+



ERROR:root:KeyboardInterrupt while sending command.
Traceback (most recent call last):
  File "/opt/miniconda3/envs/dasc_5410/lib/python3.11/site-packages/py4j/java_gateway.py", line 1038, in send_command
    response = connection.send_command(command)
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/opt/miniconda3/envs/dasc_5410/lib/python3.11/site-packages/py4j/clientserver.py", line 511, in send_command
    answer = smart_decode(self.stream.readline()[:-1])
                          ^^^^^^^^^^^^^^^^^^^^^^
  File "/opt/miniconda3/envs/dasc_5410/lib/python3.11/socket.py", line 706, in readinto
    return self._sock.recv_into(b)
           ^^^^^^^^^^^^^^^^^^^^^^^
KeyboardInterrupt


KeyboardInterrupt: 

`.format("console")`: Specifies that the output will be written to the console. Other options include:
- **Console Sink**: Writes output to the console.
- **File Sink**: Writes output to files (CSV, JSON, Parquet).
- **Kafka Sink**: Writes output to a Kafka topic.
- **Memory Sink**: Writes output to an in-memory table.
- **Delta Lake Sink**: Writes output to a Delta Lake table.
- **Foreach Sink**: Allows custom logic for each row in the output.

`.outputMode("complete")`: Sets the output mode to "complete", meaning the entire result table is output each time it is updated.

`.start()`: Starts the streaming query.

`.awaitTermination()`: Blocks the current thread and waits for the streaming query to terminate.

In Spark Structured Streaming, there are three common output modes for writing streaming data:

### 1. **Append Mode**
- **Description**: Only the new rows added to the result table since the last trigger are written to the sink.
- **Usage**:
  ```python
  df_agg.writeStream.format("console").outputMode("append").start().awaitTermination()
  ```
- **Use Case**: Suitable for scenarios where you only need to process and output new data, such as appending new log entries or sensor readings.

### 2. **Complete Mode**
- **Description**: The entire result table is written to the sink every time it is updated.
- **Usage**:
  ```python
  df_agg.writeStream.format("console").outputMode("complete").start().awaitTermination()
  ```
- **Use Case**: Useful for aggregations where you need to output the entire result, such as computing running totals or averages.

### 3. **Update Mode**
- **Description**: Only the rows that were updated in the result table since the last trigger are written to the sink.
- **Usage**:
  ```python
  df_agg.writeStream.format("console").outputMode("update").start().awaitTermination()
  ```
- **Use Case**: Suitable for scenarios where you need to update existing records, such as maintaining a running count or updating the status of records.


## Example 2: Spark Streaming Read from Files

In today's example, we will attempt to create a Spark Streaming pipeline for a weather recording application. In this context, we have a device that records the temperature and produce a log in `json` format for each reading. 

Here's an example of a reading stored in a `json` format:

```json
{
  "eventId": "e3cb26d3-41b2-49a2-84f3-0156ed8d7502",
  "eventOffset": 10001,
  "eventPublisher": "device",
  "customerId": "CI00103",
  "data": {
    "devices": [
      {
        "deviceId": "D001",
        "temperature": 15,
        "measure": "C",
        "status": "ERROR"
      },
      {
        "deviceId": "D002",
        "temperature": 16,
        "measure": "C",
        "status": "SUCCESS"
      }
    ]
  },
  "eventTime": "2023-01-05 11:13:53.643364"
}
```

### Task

Our goal here is to pre-process this `json` file as it comes in. We will flatten the data and store them in a single `csv` file.

The output should look like this

| customerId | eventId                               | eventOffset | eventPublisher | eventTime           | deviceId | measure | status  | temperature |
|------------|---------------------------------------|-------------|----------------|---------------------|----------|---------|---------|-------------|
| CI00108    | aa90011f-3967-496...                  | 10003       | device         | 2023-01-05 11:13:...| D004     | C       | SUCCESS | 16          |


### Code

#### 1. Initialize a SparkSession

In [ ]:
# Create the Spark Session
from pyspark.sql import SparkSession

spark = (
    SparkSession.builder
    .appName("Weather streaming")
    .config("spark.streaming.stopGracefullyOnShutdown", "true")
    .master("local[*]")
    .getOrCreate()
)

spark

- `SparkSession.builder`: This is a builder pattern used to configure and create a SparkSession instance.
- `appName("Streaming Process Files")`: Sets the name of the Spark application. This name will appear in the Spark web UI and logs.
- `config("spark.streaming.stopGracefullyOnShutdown", True)`: Configures Spark to stop streaming jobs gracefully on shutdown. This means that Spark will try to complete the ongoing tasks before shutting down.
- `master("local[*]")`: Sets the master URL to connect to. In this case, local[*] means that Spark will run locally with as many worker threads as logical cores on your machine.
- `getOrCreate()`: This method either retrieves an existing SparkSession or creates a new one if none exists.

#### 2. Import data

In [47]:
# Enable automatic schema inference for streaming data
# This allows Spark to automatically infer the schema of the JSON files being read
spark.conf.set("spark.sql.streaming.schemaInference", True)

streaming_df = (
    spark.readStream
    .option("cleanSource", "archive")
    .option("sourceArchiveDir", "data/archive/")
    .option("maxFilesPerTrigger", 1)
    .format("json")
    .load("data/input/")
)

In [48]:
streaming_df.printSchema()
# streaming_df.show()

root
 |-- customerId: string (nullable = true)
 |-- data: struct (nullable = true)
 |    |-- devices: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- deviceId: string (nullable = true)
 |    |    |    |-- measure: string (nullable = true)
 |    |    |    |-- status: string (nullable = true)
 |    |    |    |-- temperature: long (nullable = true)
 |-- eventId: string (nullable = true)
 |-- eventOffset: long (nullable = true)
 |-- eventPublisher: string (nullable = true)
 |-- eventTime: string (nullable = true)



#### 3. Explode the data

In [49]:
# Lets explode the data as devices contains list/array of device reading
from pyspark.sql.functions import explode

exploded_df = streaming_df.withColumn("data_devices", explode("data.devices"))

In [50]:
# Check the schema of the exploded_df, place a sample json file and change readStream to read 
exploded_df.printSchema()
# exploded_df.show(truncate=False)

root
 |-- customerId: string (nullable = true)
 |-- data: struct (nullable = true)
 |    |-- devices: array (nullable = true)
 |    |    |-- element: struct (containsNull = true)
 |    |    |    |-- deviceId: string (nullable = true)
 |    |    |    |-- measure: string (nullable = true)
 |    |    |    |-- status: string (nullable = true)
 |    |    |    |-- temperature: long (nullable = true)
 |-- eventId: string (nullable = true)
 |-- eventOffset: long (nullable = true)
 |-- eventPublisher: string (nullable = true)
 |-- eventTime: string (nullable = true)
 |-- data_devices: struct (nullable = true)
 |    |-- deviceId: string (nullable = true)
 |    |-- measure: string (nullable = true)
 |    |-- status: string (nullable = true)
 |    |-- temperature: long (nullable = true)



#### 4. Flatten the exploded data

In [51]:
# Flatten the exploded df
from pyspark.sql.functions import col

flattened_df = (
    exploded_df
    .drop("data")
    .withColumn("deviceId", col("data_devices.deviceId"))
    .withColumn("measure", col("data_devices.measure"))
    .withColumn("status", col("data_devices.status"))
    .withColumn("temperature", col("data_devices.temperature"))
    .drop("data_devices")
)


In [52]:
# Check the schema of the flattened_df, place a sample json file and change readStream to read 
flattened_df.printSchema()
# flattened_df.show(truncate=False)

root
 |-- customerId: string (nullable = true)
 |-- eventId: string (nullable = true)
 |-- eventOffset: long (nullable = true)
 |-- eventPublisher: string (nullable = true)
 |-- eventTime: string (nullable = true)
 |-- deviceId: string (nullable = true)
 |-- measure: string (nullable = true)
 |-- status: string (nullable = true)
 |-- temperature: long (nullable = true)



#### 5. Write the output to console or csv file

In [53]:
# Write the output to console sink to check the output
(flattened_df.writeStream
 .format("console")
 .outputMode("append")
 .start().awaitTermination())

# Write the output to csv sink
# (flattened_df.writeStream
#  .format("csv")
#  .outputMode("append")
#  .option("path", "data/output/device_output.csv")
#  .option("checkpointLocation", "data/checkpoint/device_output")
#  .start().awaitTermination())


24/11/20 12:10:14 WARN ResolveWriteToStream: Temporary checkpoint location created which is deleted normally when the query didn't fail: /private/var/folders/vs/gmr4pxqx5fjg8p7kzzwgwqbw0000gn/T/temporary-abe7c78e-2b9d-4936-b6e8-f2b7b46867b2. If it's required to delete it under any circumstances, please set spark.sql.streaming.forceDeleteTempCheckpointLocation to true. Important to know deleting temp checkpoint folder is best effort.
24/11/20 12:10:14 WARN ResolveWriteToStream: spark.sql.adaptive.enabled is not supported in streaming DataFrames/Datasets and will be disabled.


-------------------------------------------
Batch: 0
-------------------------------------------
+----------+--------------------+-----------+--------------+--------------------+--------+-------+-------+-----------+
|customerId|             eventId|eventOffset|eventPublisher|           eventTime|deviceId|measure| status|temperature|
+----------+--------------------+-----------+--------------+--------------------+--------+-------+-------+-----------+
|   CI00103|e3cb26d3-41b2-49a...|      10001|        device|2023-01-05 11:13:...|    D001|      C|  ERROR|         15|
|   CI00103|e3cb26d3-41b2-49a...|      10001|        device|2023-01-05 11:13:...|    D002|      C|SUCCESS|         16|
+----------+--------------------+-----------+--------------+--------------------+--------+-------+-------+-----------+



ERROR:root:KeyboardInterrupt while sending command.
Traceback (most recent call last):
  File "/opt/miniconda3/envs/dasc_5410/lib/python3.11/site-packages/py4j/java_gateway.py", line 1038, in send_command
    response = connection.send_command(command)
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/opt/miniconda3/envs/dasc_5410/lib/python3.11/site-packages/py4j/clientserver.py", line 511, in send_command
    answer = smart_decode(self.stream.readline()[:-1])
                          ^^^^^^^^^^^^^^^^^^^^^^
  File "/opt/miniconda3/envs/dasc_5410/lib/python3.11/socket.py", line 706, in readinto
    return self._sock.recv_into(b)
           ^^^^^^^^^^^^^^^^^^^^^^^
KeyboardInterrupt


KeyboardInterrupt: 